In [1]:
import typing as T

import numpy as np
import numpy.typing as npt
import scipy as sp

from matplotlib import pyplot as plt
import matplotlib.patches as patches

from pydrake.solvers import (
    MathematicalProgram,
    MathematicalProgramResult,
    Solve,
    SolverOptions,
    CommonSolverOption, 
    IpoptSolver,
    GurobiSolver
)
from pydrake.symbolic import Polynomial, Variable, Variables, Evaluate
from sdp import create_sdp_relaxation, _get_sol_from_svd

from pydrake.math import eq, le, ge

from util import timeit, YAY, WARN, INFO, ERROR

In [2]:
import math

import matplotlib.pyplot as plt
import mpld3
import numpy as np
from IPython.display import HTML, display
from pydrake.all import (
    AddMultibodyPlantSceneGraph,
    ControllabilityMatrix,
    DiagramBuilder,
    Linearize,
    LinearQuadraticRegulator,
    MeshcatVisualizer,
    Parser,
    Saturation,
    SceneGraph,
    Simulator,
    StartMeshcat,
    WrapToSystem,
)
from pydrake.examples import (
    AcrobotGeometry,
    AcrobotInput,
    AcrobotPlant,
    AcrobotState,
    QuadrotorGeometry,
    QuadrotorPlant,
    StabilizingLQRController,
)
from pydrake.solvers import MathematicalProgram, Solve

# from underactuated import ConfigureParser, running_as_notebook
from underactuated import running_as_notebook
from underactuated.meshcat_utils import MeshcatSliders
from underactuated.quadrotor2d import Quadrotor2D, Quadrotor2DVisualizer

if running_as_notebook:
    mpld3.enable_notebook()

In [ ]:
# Start the visualizer (run this cell only once, each instance consumes a port)
meshcat = StartMeshcat()

INFO:drake:Meshcat listening for connections at http://localhost:7001


In [11]:
def planar_quadrotor_example():
    def QuadrotorLQR(plant):
        context = plant.CreateDefaultContext()
        # desired state is 0
        context.SetContinuousState(np.zeros([6, 1]))
        # desired control counteracts gravity
        plant.get_input_port(0).FixValue(context, plant.mass * plant.gravity / 2.0 * np.array([1, 1]))
        # Q R matrices
        Q = np.diag([10, 10, 10, 1, 1, (plant.length / 2.0 / np.pi)])
        R = np.array([[0.1, 0.05], [0.05, 0.1]])
        # pass plant and context
        return LinearQuadraticRegulator(plant, context, Q, R)

    builder = DiagramBuilder()
    plant = builder.AddSystem(Quadrotor2D())

    controller = builder.AddSystem(QuadrotorLQR(plant))
    builder.Connect(controller.get_output_port(0), plant.get_input_port(0))
    builder.Connect(plant.get_output_port(0), controller.get_input_port(0))

    # Setup visualization
    visualizer = builder.AddSystem(Quadrotor2DVisualizer(show=False))
    builder.Connect(plant.get_output_port(0), visualizer.get_input_port(0))

    diagram = builder.Build()

    # Set up a simulator to run this diagram
    simulator = Simulator(diagram)
    context = simulator.get_mutable_context()

    # Simulate
    duration = 4.0 if running_as_notebook else 0.1
    visualizer.start_recording()
    print("simulating...")

    # simulate from random initial conditions
    for i in range(5):
        context.SetTime(0.0)
        context.SetContinuousState( np.random.randn(6,))
        simulator.Initialize()
        simulator.AdvanceTo(duration)
    print("done.\ngenerating animation...")
    ani = visualizer.get_recording_as_animation()
    display(HTML(ani.to_jshtml()))


planar_quadrotor_example()

# vis = Quadrotor2DVisualizer(show=False)
# ani = vis.animate(x_trajectory)
# display(HTML(ani.to_jshtml()))

simulating...
done.
generating animation...


In [8]:
builder = DiagramBuilder()
plant = builder.AddSystem(Quadrotor2D())

def make_a_nonconvex_birotor_program(N, plant, init_pos=np.zeros(2), desired_pos = np.array([2,0]), dt = 0.25, custom_dt_12 = False, for_sdp_solver = False):
    # stabilize trajectory using finite horizon LQR? 
    if custom_dt_12:
        N = 12
        dt = np.array([ 0.1, 0.1, 0.1,  0.15, 0.15, 0.15,  0.2, 0.2, 0.2,  0.2, 0.2, 0.2 ])

    thrust_2_mass_ratio = 3 # 3:1 thrust : mass ratio
    r = plant.length
    m = plant.mass
    I = plant.inertia
    g = plant.gravity

    Q = np.diag([10, 10, 10, 1, 1, (r / 2.0 / np.pi), 10, 10 ])
    Qf = Q
    R = np.array([[0.1, 0.05], [0.05, 0.1]])


    prog = MathematicalProgram()
    # define optimization variables
    # N+1 timesteps for each state
    x = prog.NewContinuousVariables(N+1, "x")
    y = prog.NewContinuousVariables(N+1, "y")
    th = prog.NewContinuousVariables(N+1, "th")
    dx = prog.NewContinuousVariables(N+1, "dx")
    dy = prog.NewContinuousVariables(N+1, "dy")
    dth = prog.NewContinuousVariables(N+1, "dth")
    c = prog.NewContinuousVariables(N+1, "c")
    s = prog.NewContinuousVariables(N+1, "s")
    # N timesteps for control inputs
    v = prog.NewContinuousVariables(N, "v")
    w = prog.NewContinuousVariables(N, "w")
    # full state and control vectors
    z = np.vstack( (x,y,th,dx,dy,dth,c,s) ).T

    u = np.vstack( (v,w) ).T

    # cos^2 + sin^2 = 1
    if for_sdp_solver:
        # bounds on state (for solver's sake)
        prog.AddConstraint(eq( s ** 2 + c ** 2, 1 ))

        prog.AddBoundingBoxConstraint(-5*np.ones(N+1),  5*np.ones(N+1),  x)
        prog.AddBoundingBoxConstraint(-5*np.ones(N+1),  5*np.ones(N+1),  y)
        prog.AddBoundingBoxConstraint( -np.pi*np.ones(N+1),  np.pi*np.ones(N+1),  th)
        # prog.AddBoundingBoxConstraint( -10*np.ones(N+1),  10*np.ones(N+1),  dx)
        # prog.AddBoundingBoxConstraint( -10*np.ones(N+1),  10*np.ones(N+1),  dy)
        # prog.AddBoundingBoxConstraint( -np.pi*3*np.ones(N+1),  np.pi*3*np.ones(N+1),  dth)

        # prog.AddBoundingBoxConstraint(-1, 1, c)
        # prog.AddBoundingBoxConstraint(-1, 1, s)
        # prog.AddConstraint(le( s ** 2 + c ** 2, 1.02 ))
        # prog.AddConstraint(ge( s ** 2 + c ** 2, 0.98 ))
        # print(ge( s ** 2 + c ** 2, 0.98 ))
        # print(ge( s ** 2 + c ** 2, 0.98 ))
    else:
        # if solving with nonlinear solver -- relax cos^2 + sin^2 = 1, add bounding boxes
        prog.AddConstraint(le( s ** 2 + c ** 2, 1.05 ))
        prog.AddConstraint(le( 0.95, s ** 2 + c ** 2 ))
        prog.AddBoundingBoxConstraint(-5*np.ones(N+1),  5*np.ones(N+1),  x)
        prog.AddBoundingBoxConstraint(-5*np.ones(N+1),  5*np.ones(N+1),  y)
        prog.AddBoundingBoxConstraint( -np.pi*np.ones(N+1),  np.pi*np.ones(N+1),  th)
        prog.AddBoundingBoxConstraint( -10*np.ones(N+1),  10*np.ones(N+1),  dx)
        prog.AddBoundingBoxConstraint( -10*np.ones(N+1),  10*np.ones(N+1),  dy)
        prog.AddBoundingBoxConstraint( -np.pi*3*np.ones(N+1),  np.pi*3*np.ones(N+1),  dth)
        prog.AddBoundingBoxConstraint(-1, 1, c)
        prog.AddBoundingBoxConstraint(-1, 1, s)
    # dynamics
    prog.AddConstraint( eq( x[1:], x[:-1] + dt * dx[:-1] ) )
    prog.AddConstraint( eq( y[1:], y[:-1] + dt * dy[:-1] ) )
    prog.AddConstraint( eq( th[1:], th[:-1] + dt * dth[:-1] ) )
    prog.AddConstraint( eq( dx[1:], dx[:-1] + dt * (-(v + w) * s[:-1] / m) ) )
    prog.AddConstraint( eq( dy[1:], dy[:-1] + dt * ( (v + w) * c[:-1] / m - g) ) )
    prog.AddConstraint( eq( dth[1:], dth[:-1] + dt * (v - w) * r / I ) )
    prog.AddConstraint( eq( c[1:], c[:-1] - dt * dth[:-1] * s[:-1] ) )
    prog.AddConstraint( eq( s[1:], s[:-1] + dt * dth[:-1] * c[:-1] ) )
    # lower and upper bounds on control inputs
    prog.AddBoundingBoxConstraint(0, m*g/2 * thrust_2_mass_ratio, v)
    prog.AddBoundingBoxConstraint(0, m*g/2 * thrust_2_mass_ratio, w)
    
    # initial constraints
    z_0 = np.hstack( (init_pos, np.array([0, 0,0,0, 1,0]) ))
    prog.AddConstraint( eq( z[0], z_0 ) )
    # desired point
    z_star = np.hstack( (desired_pos, np.array([0, 0,0,0, 1,0]) ))
    u_star = m * g / 2.0 * np.array([1, 1])

    # build the cost
    cost = 0
    for i in range(N):
        cost = cost + (z[i]-z_star).dot(Q).dot(z[i]-z_star) + (u[i]-u_star).dot(R).dot(u[i]-u_star)
    cost += (z[N]-z_star).dot(Qf).dot(z[N]-z_star)
    prog.AddCost(cost)

    if for_sdp_solver:
        return prog

    print("Program built.")
    timer = timeit()
    solution = Solve(prog)
    timer.dt("Program solved.")
    
    if not solution.is_success():
        ERROR("solve failed")
    else:
        YAY("solved!")
    print(solution.get_solver_id())
    print(solution.get_optimal_cost())
    print(solution.get_solution_result())

    INFO( "x", np.round(solution.GetSolution(x),2) )
    INFO( "y",  np.round(solution.GetSolution(y),2) )
    INFO( "th", np.round(solution.GetSolution(th),2) )
    print("---")
    INFO( "dx", np.round(solution.GetSolution(dx),2) )
    INFO( "dy",  np.round(solution.GetSolution(dy),2) )
    INFO( "dth", np.round(solution.GetSolution(dth),2) )
    print("---")
    INFO( "v", np.round(solution.GetSolution(v),2) )
    INFO( "w",  np.round(solution.GetSolution(w),2) )
    return prog, solution
    
N = 5
prog = make_a_nonconvex_birotor_program(N, plant, dt = 0.2, custom_dt_12 = False, for_sdp_solver = True)

In [9]:
relaxed_prog, X, basis = create_sdp_relaxation(prog)

# are all the constraints satisfied?
# could it be that Bernhard's implementation is missing something
# check that dynamics cosntraints hold

making decision vars
colleciting bounding box constraints
adding quadratic costs: 1
adding linear equality constraints: 5
adding linear inequality constraints: 56
adding generic constraints: 5
      _generic_constraint_bindings_to_polynomials
      concatenate
      _quadratic_polynomial_to_homoenuous_form
      q-eqs
ues
ues
ues
ues
ues
ues
ues
ues
ues
ues
ues
ues
ues
ues
ues
ues
ues
ues
ues
ues
ues
ues
ues
ues
ues
ues
      q-ineqs


In [10]:
timer = timeit()
relaxed_solution = Solve(relaxed_prog)
timer.dt()
print(relaxed_solution.is_success())
print(relaxed_solution.get_optimal_cost())
print(relaxed_solution.get_solution_result())

4.518s since last time-check
True
247.275944848196
SolutionResult.kSolutionFound


In [11]:
# X np.round(relaxed_solution.GetSolution(X),2)
X_val = relaxed_solution.GetSolution(X)
print(X_val.shape)
print(np.linalg.matrix_rank(X_val))


(59, 59)
11


In [45]:
x_val = X_val[:, 0]
rounded_sols = np.round(np.real(_get_sol_from_svd(X_val)),3)

In [12]:
for i in range(59):
    # if i > 13:
    print(X_val[i,i])

0.9999999999998794
3.0379427908123417e-13
3.0379364036108924e-13
3.2047504719332467e-13
0.1993882228160941
0.4511403155604624
0.5859572211727188
3.0377625223942637e-13
3.0378337799091397e-13
0.0014404678548763188
0.0004412585768087206
0.00015528347144454647
7.922626478810862e-05
3.0377518362795593e-13
3.0377760768519373e-13
3.0929086976797346e-13
3.005614426692034e-13
2.920762713050941e-13
2.8389546568960565e-13
3.2187100969014395e-13
7.146557715170344e-13
4.984705570403236
1.2672085114061062
0.22000147564760567
1.919879956338056e-13
3.0402808005294553e-13
0.036011696364460374
0.007180308551770239
0.001825372991811397
0.0003169050061915357
1.9198799563381055e-13
3.0584408171460527e-13
4.4149952534229214e-13
7.692122455771715e-13
7.631402585730415e-13
7.828803905136025e-13
4.799121759796819e-12
0.9999999999998237
0.9999999999976791
0.24999999645275697
0.24999999645275622
0.24999999645275664
0.2499999964527571
3.3079570089680914e-13
1.926930195637801e-14
1.9269301956375704e-14
1.92693019

In [55]:
# does the c+s constraint not hold
N2+=1
print( X_val[N2+5*N1,N2+5*N1] )
print( X_val[N2+6*N1,N2+6*N1] )

3.3079570089680914e-13
4.636539446151489


In [56]:
N = 5
N1 = 6
N2 = 7
print("x", rounded_sols[1:N2])
print("y", rounded_sols[N2: N2+N1])
print("th", rounded_sols[N2+N1: N2+2*N1])
print("dx", rounded_sols[N2+2*N1: N2+3*N1])
print("dy", rounded_sols[N2+3*N1: N2+4*N1])
print("dth", rounded_sols[N2+4*N1: N2+5*N1])
print("c", rounded_sols[N2+5*N1: N2+6*N1])
print("s", rounded_sols[N2+6*N1: N2+7*N1])
print("v", rounded_sols[N2+7*N1: N2+7*N1+N])
print("w", rounded_sols[N2+7*N1+N: N2+7*N1+2*N])

x [-0.    -0.    -0.     0.447  0.672  0.765]
y [-0.    -0.    -0.038 -0.021 -0.012 -0.009]
th [-0.  0.  0.  0.  0.  0.]
dx [-0.    -0.     2.233  1.126  0.469  0.   ]
dy [-0.    -0.19   0.085  0.043  0.018  0.   ]
dth [ 0.  0. -0.  0. -0.  0.]
c [1.  1.  0.5 0.5 0.5 0.5]
s [ 0.  0. -0. -0. -0.  0.]
v [2.153 1.192 1.192 1.192 1.192]
w [2.153 1.192 1.192 1.192 1.192]


In [27]:
# x [ 0.    0.   -0.   -0.    0.14  0.36]
# y [ 0.    0.   -0.01 -0.13 -0.01  0.06]
# th [ 0.   -0.   -0.22 -0.22 -0.22 -0.22]
# ---
# dx [-0.   -0.   -0.    0.72  1.09  1.43]
# dy [-0.   -0.05 -0.61  0.62  0.32 -0.12]
# dth [-0.   -1.12  0.    0.   -0.   -0.  ]
# ---
# v [2.28 1.74 3.89 2.01 1.85]
# w [2.37 1.65 3.89 2.01 1.85]

array([<Monomial "1">, <Monomial "x(0)">, <Monomial "x(1)">, ...,
       <Monomial "w(3)^2">, <Monomial "w(3) * w(4)">, <Monomial "w(4)^2">],
      dtype=object)

In [41]:
rounded_sols

array([ 1.   , -0.   , -0.   , -0.   ,  0.447,  0.672,  0.765, -0.   ,
       -0.   , -0.038, -0.021, -0.012, -0.009, -0.   ,  0.   ,  0.   ,
        0.   ,  0.   ,  0.   , -0.   , -0.   ,  2.233,  1.126,  0.469,
        0.   , -0.   , -0.19 ,  0.085,  0.043,  0.018,  0.   ,  0.   ,
        0.   , -0.   ,  0.   , -0.   ,  0.   ,  1.   ,  1.   ,  0.5  ,
        0.5  ,  0.5  ,  0.5  ,  0.   ,  0.   , -0.   , -0.   , -0.   ,
        0.   ,  2.153,  1.192,  1.192,  1.192,  1.192,  2.153,  1.192,
        1.192,  1.192,  1.192])

In [61]:
np.sqrt(1-0.25*0.25)

0.9682458365518543